In [0]:
from google.colab import drive
drive.mount("/content/gdrive")

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/gdrive


In [0]:
from google.colab import drive
import numpy as np
import scipy.io
import pandas as pd
from datetime import datetime, timedelta
import os
import tensorflow as tf
import keras
from keras.preprocessing import image
from keras.callbacks import ModelCheckpoint,EarlyStopping
from keras.layers import Dense, Activation, Dropout, Flatten, Input, \
Convolution2D, ZeroPadding2D, MaxPooling2D
from keras.layers import Conv2D, AveragePooling2D
from keras.models import Model, Sequential
from sklearn.model_selection import train_test_split
from keras import metrics
from keras.models import model_from_json
import matplotlib.pyplot as plt
from glob import glob
import math
import shutil
import re
import cv2
from PIL import Image
from keras.preprocessing.image import load_img, save_img, img_to_array, ImageDataGenerator
from keras.applications.imagenet_utils import preprocess_input
from os import listdir

Using TensorFlow backend.


In [1]:
# download dataset from drive
!gdown --id 1Yc4JhKcwP3j_9MCv_U5eb_f_L1mHeqmJ

Downloading...
From: https://drive.google.com/uc?id=1Yc4JhKcwP3j_9MCv_U5eb_f_L1mHeqmJ
To: /content/final crop faces.zip
351MB [00:05, 85.5MB/s]Traceback (most recent call last):
  File "/usr/local/bin/gdown", line 8, in <module>
    sys.exit(main())
  File "/usr/local/lib/python2.7/dist-packages/gdown/cli.py", line 61, in main
    quiet=args.quiet,
  File "/usr/local/lib/python2.7/dist-packages/gdown/download.py", line 101, in download
    for chunk in res.iter_content(chunk_size=CHUNK_SIZE):
  File "/usr/local/lib/python2.7/dist-packages/requests/models.py", line 750, in generate
    for chunk in self.raw.stream(chunk_size, decode_content=True):
  File "/usr/local/lib/python2.7/dist-packages/urllib3/response.py", line 492, in stream
    for line in self.read_chunked(amt, decode_content=decode_content):
  File "/usr/local/lib/python2.7/dist-packages/urllib3/response.py", line 668, in read_chunked
    self._update_chunk_length()
  File "/usr/local/lib/python2.7/dist-packages/urllib3/res

In [0]:
!unzip /content/gdrive/'My Drive'/'final crop faces.zip'

Archive:  /content/gdrive/My Drive/final crop faces.zip
   creating: final crop faces/
   creating: final crop faces/42/
  inflating: final crop faces/42/42crop2871.jpg  
  inflating: final crop faces/42/42crop2873.jpg  
  inflating: final crop faces/42/42crop2877.jpg  
  inflating: final crop faces/42/42crop2879.jpg  
  inflating: final crop faces/42/42crop2883.jpg  
  inflating: final crop faces/42/42crop2888.jpg  
  inflating: final crop faces/42/42crop2889.jpg  
  inflating: final crop faces/42/42crop2891.jpg  
  inflating: final crop faces/42/42_wiki_122__34_633934_1969-10-23_2011crop2892.jpg  
  inflating: final crop faces/42/42crop2895.jpg  
  inflating: final crop faces/42/42crop2897.jpg  
  inflating: final crop faces/42/42crop2899.jpg  
  inflating: final crop faces/42/42crop2911.jpg  
  inflating: final crop faces/42/42_wiki_57__12_1618912_1970-07-22_2012crop2912.jpg  
  inflating: final crop faces/42/42crop2913.jpg  
  inflating: final crop faces/42/42crop2914.jpg  
  infla

In [0]:
# os.rename("cleaned", "Main")

In [0]:
# !mv /content/20 Main


### Pre-Trained weights Download

Downloading...
From: https://drive.google.com/uc?id=1Yc4JhKcwP3j_9MCv_U5eb_f_L1mHeqmJ
To: /content/final crop faces.zip
1.08GB [00:06, 155MB/s]


In [0]:
# vgg face model
!gdown --id 1CPSeum3HpopfomUEK1gybeuIVoeJT_Eo

Downloading...
From: https://drive.google.com/uc?id=1CPSeum3HpopfomUEK1gybeuIVoeJT_Eo
To: /content/vgg_face_weights.h5
580MB [00:04, 121MB/s]


In [0]:
# age weights
!gdown --id 1YCox_4kJ-BYeXq27uUbasu--yz28zUMV

Downloading...
From: https://drive.google.com/uc?id=1YCox_4kJ-BYeXq27uUbasu--yz28zUMV
To: /content/age_model_weights.h5
539MB [00:04, 115MB/s]


# VGG

In [0]:
#os.rename("cleaned", "Main")

In [0]:
# !rm Main/41/41.0_imdb_100__01_nm0001001_rm2306718464_1940-3-26_1981.jpg

In [0]:

IMAGE_SIZE = [224,224]
path='/content/final crop faces'
# preprocessing_function is applied on each image but only after re-sizing & augmentation (resize => augment => pre-process)
# Each of the keras.application.resnet* preprocess_input MOSTLY mean BATCH NORMALIZATION (applied on each batch) stabilize the inputs to nonlinear activation functions
# Batch Normalization helps in faster convergence
data_generator = ImageDataGenerator(rescale = 1./255,validation_split= 0.2)

training_set = data_generator.flow_from_directory(path, target_size=IMAGE_SIZE, class_mode='categorical',
                                          subset= 'training', shuffle = True, batch_size=256)
test_set = data_generator.flow_from_directory(path, target_size=IMAGE_SIZE, class_mode='categorical',
                                      subset= 'validation', shuffle=True, batch_size=256)

Found 94084 images belonging to 100 classes.
Found 23471 images belonging to 100 classes.


In [0]:
nb_classes = training_set.num_classes

In [0]:
# nb_classes

100

In [0]:
def loadVggFaceModel():
	model = Sequential()
	model.add(ZeroPadding2D((1,1),input_shape=(224,224, 3)))
	model.add(Convolution2D(64, (3, 3), activation='relu'))
	model.add(ZeroPadding2D((1,1)))
	model.add(Convolution2D(64, (3, 3), activation='relu'))
	model.add(MaxPooling2D((2,2), strides=(2,2)))

	model.add(ZeroPadding2D((1,1)))
	model.add(Convolution2D(128, (3, 3), activation='relu'))
	model.add(ZeroPadding2D((1,1)))
	model.add(Convolution2D(128, (3, 3), activation='relu'))
	model.add(MaxPooling2D((2,2), strides=(2,2)))

	model.add(ZeroPadding2D((1,1)))
	model.add(Convolution2D(256, (3, 3), activation='relu'))
	model.add(ZeroPadding2D((1,1)))
	model.add(Convolution2D(256, (3, 3), activation='relu'))
	model.add(ZeroPadding2D((1,1)))
	model.add(Convolution2D(256, (3, 3), activation='relu'))
	model.add(MaxPooling2D((2,2), strides=(2,2)))

	model.add(ZeroPadding2D((1,1)))
	model.add(Convolution2D(512, (3, 3), activation='relu'))
	model.add(ZeroPadding2D((1,1)))
	model.add(Convolution2D(512, (3, 3), activation='relu'))
	model.add(ZeroPadding2D((1,1)))
	model.add(Convolution2D(512, (3, 3), activation='relu'))
	model.add(MaxPooling2D((2,2), strides=(2,2)))

	model.add(ZeroPadding2D((1,1)))
	model.add(Convolution2D(512, (3, 3), activation='relu'))
	model.add(ZeroPadding2D((1,1)))
	model.add(Convolution2D(512, (3, 3), activation='relu'))
	model.add(ZeroPadding2D((1,1)))
	model.add(Convolution2D(512, (3, 3), activation='relu'))
	model.add(MaxPooling2D((2,2), strides=(2,2)))

	model.add(Convolution2D(4096, (7, 7), activation='relu'))
	model.add(Dropout(0.5))
	model.add(Convolution2D(4096, (1, 1), activation='relu'))
	model.add(Dropout(0.5))
	model.add(Convolution2D(2622, (1, 1)))
	model.add(Flatten())
	model.add(Activation('softmax'))
	
	return model

In [0]:
model = loadVggFaceModel()






Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


In [0]:
model.load_weights('vgg_face_weights.h5')

In [0]:
for layer in model.layers[:-7]:
    layer.trainable = False
 
base_model_output = Sequential()
base_model_output = Convolution2D(nb_classes, (1, 1), name='predictions')(model.layers[-4].output)
base_model_output = Dropout(0.5)(base_model_output)
base_model_output = Flatten()(base_model_output)
base_model_output = Dense(128, kernel_regularizer= keras.regularizers.l2(l=0.005))(base_model_output)
base_model_output = Activation('relu')(base_model_output)
base_model_output = Dense(nb_classes)(base_model_output)
base_model_output = Activation('softmax')(base_model_output)
base_model_output = Dropout(0.3)(base_model_output)
 
age_model = Model(inputs=model.input, outputs=base_model_output)

age_model.compile(loss = 'categorical_crossentropy', optimizer = 'adam', metrics = ['accuracy'])

In [0]:
checkpointer = ModelCheckpoint(
    filepath='/content/gdrive/My Drive/age_weights.hdf5'
    , monitor = "val_loss"
    , verbose=1
    , save_weights_only=True
    , mode = 'auto'
)

In [0]:
age_model.fit_generator(training_set, steps_per_epoch=int(len(training_set)/4),
                        epochs = 200, validation_data=test_set, 
                        validation_steps = int(len(test_set)), verbose=1,
                        callbacks = [checkpointer])

Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


Epoch 1/200
92/92 [==============================] - 145s 2s/step - loss: 7.7681 - acc: 0.0424 - val_loss: 3.8368 - val_acc: 0.0697

Epoch 00001: saving model to /content/gdrive/My Drive/age_weights.hdf5
Epoch 2/200
92/92 [==============================] - 128s 1s/step - loss: 7.1820 - acc: 0.0668 - val_loss: 3.6660 - val_acc: 0.0724

Epoch 00002: saving model to /content/gdrive/My Drive/age_weights.hdf5
Epoch 3/200
92/92 [==============================] - 131s 1s/step - loss: 7.0898 - acc: 0.0732 - val_loss: 3.5213 - val_acc: 0.0783

Epoch 00003: saving model to /content/gdrive/My Drive/age_weights.hdf5
Epoch 4/200
92/92 [==============================] - 128s 1s/step - loss: 7.0327 - acc: 0.0803 - val_loss: 3.5197 - val_acc: 0.0776

Epoch 00004: saving model to /content/gdrive/My Drive/age_weights.hdf5
Epoch 5/200
92/92 [==============================] - 128s 1s/step - loss: 6.9320 - acc: 

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.6/dist-packages/IPython/core/interactiveshell.py", line 2882, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-14-da73338a35a5>", line 4, in <module>
    callbacks = [checkpointer])
  File "/usr/local/lib/python3.6/dist-packages/keras/legacy/interfaces.py", line 91, in wrapper
    return func(*args, **kwargs)
  File "/usr/local/lib/python3.6/dist-packages/keras/engine/training.py", line 1658, in fit_generator
    initial_epoch=initial_epoch)
  File "/usr/local/lib/python3.6/dist-packages/keras/engine/training_generator.py", line 237, in fit_generator
    workers=0)
  File "/usr/local/lib/python3.6/dist-packages/keras/legacy/interfaces.py", line 91, in wrapper
    return func(*args, **kwargs)
  File "/usr/local/lib/python3.6/dist-packages/keras/engine/training.py", line 1717, in evaluate_generator
    verbose=verbose)
  File "/usr/local/lib/python3.6/dist-packages/keras/engine/train

KeyboardInterrupt: ignored

In [0]:
# !ls Main/20

In [0]:
# !rm -r Main/110

In [0]:
# !tar -czvf Main.tar.gz Main

In [0]:
# test_set